# Plot yeast RBD DMS escape maps

## Import modules and read data
Import Python modules:

In [1]:
import itertools
import os

import altair as alt

import numpy

import pandas as pd

import sklearn.manifold

Disable max rows specifier for Altair:

In [2]:
_ = alt.data_transformers.disable_max_rows()

Read the deep mutational scanning data, reduce to site-level data:

In [3]:
# only site level data for escape and drop entries with 0 escape which we impute below
dms_data = (
    pd.read_csv('./processed_data/escape_data.csv', low_memory=False)
    .assign(condition_alias=lambda x: x['condition_alias'].fillna(''))
    .rename(columns={"site_total_escape": "escape"})
    .query("escape != 0")
    [['condition', 'condition_alias', 'condition_type', 'condition_subtype',
      'eliciting_virus', 'known_to_neutralize', 'study', 'lab', 'site', "escape"]]
    .drop_duplicates()
)

# get list of all sites
sites = list(range(dms_data['site'].min(), dms_data['site'].max() + 1))

# for duplicated conditions, add lab to name
dms_data = (
    dms_data
    .assign(
        n_studies=lambda x: x.groupby('condition')['study'].transform('nunique'),
        condition=lambda x: x['condition'].where(
            x['n_studies'] == 1,
            x['condition'] + ' (' + x['lab'] + ')'
        ),
    )
    .drop(columns='n_studies')
)

# for duplicated conditions within lab, keep one with more known_to_neutralize details
print(f"Before de-duplicating we have {len(dms_data.groupby(['condition', 'study']))} conditions")
dms_data = (
    dms_data
    .assign(n_known_to_neutralize=lambda x: x["known_to_neutralize"].str.count(";") + 1)
    .sort_values("n_known_to_neutralize")
    .groupby("condition", as_index=False)
    .aggregate({"study": "last"})
    .merge(dms_data)
)
print(f"After de-duplicating we have {len(dms_data.groupby(['condition', 'study']))} conditions")

assert len(dms_data) == len(dms_data.groupby(['condition', 'site']))

# split out known_to_neutralize and eliciting virus
dms_data = dms_data.assign(
    known_to_neutralize=lambda x: x["known_to_neutralize"].str.split(";").map(tuple),
    eliciting_virus=lambda x: x["eliciting_virus"].str.split(";").map(tuple),
)

dms_data

Before de-duplicating we have 1800 conditions
After de-duplicating we have 1622 conditions


condition                     study condition_alias  \
0           1-57 (Xie_XS)          2022_Cao_Omicron                   
1           1-57 (Xie_XS)          2022_Cao_Omicron                   
2           1-57 (Xie_XS)          2022_Cao_Omicron                   
3           1-57 (Xie_XS)          2022_Cao_Omicron                   
4           1-57 (Xie_XS)          2022_Cao_Omicron                   
...                   ...                       ...             ...   
46790  subject K (day 29)  2021_Greaney_HAARVI_sera                   
46791  subject K (day 29)  2021_Greaney_HAARVI_sera                   
46792  subject K (day 29)  2021_Greaney_HAARVI_sera                   
46793  subject K (day 29)  2021_Greaney_HAARVI_sera                   
46794  subject K (day 29)  2021_Greaney_HAARVI_sera                   

      condition_type   condition_subtype  \
0           antibody             class 3   
1           antibody             class 3   
2           antibody             class 3   
3           antibody             class 3   
4           antibody             class 3   
...              ...                 ...   
46790          serum  convalescent serum   
46791          serum  convalescent serum   
46792          serum  convalescent serum   
46793          serum  convalescent serum   
46794          serum  convalescent serum   

                            eliciting_virus known_to_neutralize       lab  \
0      (SARS-CoV-2, pre-Omicron SARS-CoV-2)       (Wuhan-Hu-1,)    Xie_XS   
1      (SARS-CoV-2, pre-Omicron SARS-CoV-2)       (Wuhan-Hu-1,)    Xie_XS   
2      (SARS-CoV-2, pre-Omicron SARS-CoV-2)       (Wuhan-Hu-1,)    Xie_XS   
3      (SARS-CoV-2, pre-Omicron SARS-CoV-2)       (Wuhan-Hu-1,)    Xie_XS   
4      (SARS-CoV-2, pre-Omicron SARS-CoV-2)       (Wuhan-Hu-1,)    Xie_XS   
...                                     ...                 ...       ...   
46790  (SARS-CoV-2, pre-Omicron SARS-CoV-2)       (Wuhan-Hu-1,)  Bloom_JD   
46791  (SARS-CoV-2, pre-Omicron SARS-CoV-2)       (Wuhan-Hu-1,)  Bloom_JD   
46792  (SARS-CoV-2, pre-Omicron SARS-CoV-2)       (Wuhan-Hu-1,)  Bloom_JD   
46793  (SARS-CoV-2, pre-Omicron SARS-CoV-2)       (Wuhan-Hu-1,)  Bloom_JD   
46794  (SARS-CoV-2, pre-Omicron SARS-CoV-2)       (Wuhan-Hu-1,)  Bloom_JD   

       site   escape  
0       338  0.04456  
1       370  0.03163  
2       396  0.02170  
3       444  0.03632  
4       445  0.11140  
...     ...      ...  
46790   527  0.01916  
46791   528  0.03540  
46792   529  0.11490  
46793   530  0.08733  
46794   531  0.02767  

[46795 rows x 10 columns]

Get a data frame with just the conditions and their citations:

In [4]:
conditions_df = (
    dms_data
    [['condition_type', 'condition_subtype', 'condition', 'condition_alias',
      'eliciting_virus', 'study', 'lab', 'known_to_neutralize']]
    .sort_values(['condition_type', 'condition_subtype', 'condition'])
    .drop_duplicates()
    .reset_index(drop=True)
    )

conditions_df

condition_type   condition_subtype            condition condition_alias  \
0          antibody             class 1       15033 (Xie_XS)                   
1          antibody             class 1                  2H2                   
2          antibody             class 1         B38 (Xie_XS)                   
3          antibody             class 1               BD-236                   
4          antibody             class 1               BD-319                   
...             ...                 ...                  ...             ...   
1617          serum  convalescent serum   subject I (day 26)                   
1618          serum  convalescent serum  subject J (day 121)                   
1619          serum  convalescent serum   subject J (day 15)                   
1620          serum  convalescent serum  subject K (day 103)                   
1621          serum  convalescent serum   subject K (day 29)                   

                           eliciting_virus                     study  \
0     (SARS-CoV-2, pre-Omicron SARS-CoV-2)          2022_Cao_Omicron   
1     (SARS-CoV-2, pre-Omicron SARS-CoV-2)          2022_Cao_BA2-4-5   
2     (SARS-CoV-2, pre-Omicron SARS-CoV-2)          2022_Cao_Omicron   
3     (SARS-CoV-2, pre-Omicron SARS-CoV-2)          2022_Cao_Omicron   
4     (SARS-CoV-2, pre-Omicron SARS-CoV-2)          2022_Cao_Omicron   
...                                    ...                       ...   
1617  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  2021_Greaney_HAARVI_sera   
1618  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  2021_Greaney_HAARVI_sera   
1619  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  2021_Greaney_HAARVI_sera   
1620  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  2021_Greaney_HAARVI_sera   
1621  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  2021_Greaney_HAARVI_sera   

           lab              known_to_neutralize  
0       Xie_XS                    (Wuhan-Hu-1,)  
1       Xie_XS  (Wuhan-Hu-1, Omicron BA.2.12.1)  
2       Xie_XS                    (Wuhan-Hu-1,)  
3       Xie_XS                    (Wuhan-Hu-1,)  
4       Xie_XS                    (Wuhan-Hu-1,)  
...        ...                              ...  
1617  Bloom_JD                    (Wuhan-Hu-1,)  
1618  Bloom_JD                    (Wuhan-Hu-1,)  
1619  Bloom_JD                    (Wuhan-Hu-1,)  
1620  Bloom_JD                    (Wuhan-Hu-1,)  
1621  Bloom_JD                    (Wuhan-Hu-1,)  

[1622 rows x 8 columns]

## Perform multidimensional scaling
Steps:
 1. Calculate similarities betweeen escape maps for each antibody.
 2. Convert similarities to dissimilarities.
 3. Do multi-dimensional scaling on dissimilarities.


First, compute the dissimilarity between all pairs of escape profiles in a data frame.
We calculate similarity as the dot product of the escape profile site-level metric for each pair of conditions, normalizing each profile so it's dot product with itself is one.
Then we compute the dissimilarity as just one minux the similarity:

In [5]:
def escape_similarity(df):
    """Compute similarity between all pairs of conditions in `df`."""
    df = df[['condition', 'site', 'escape']].drop_duplicates()
    assert not df.isnull().any().any(), df
    
    pivoted_df = (
        df
        .pivot_table(index='site',
                     columns='condition',
                     values='escape',
                     fill_value=0)
        # for normalization: https://stackoverflow.com/a/58113206
        # to get norm: https://stackoverflow.com/a/47953601
        .transform(lambda x: x / numpy.linalg.norm(x, axis=0))
        )
    conditions = pivoted_df.columns.tolist()
    arr = pivoted_df.values.transpose()
    similarities = [x.dot(y).sum() for x in arr for y in arr]
    return pd.DataFrame(numpy.array(similarities).reshape(len(conditions), len(conditions)),
                        columns=conditions, index=conditions)

similarities = escape_similarity(dms_data)

assert similarities.notnull().any().any()

dissimilarities = (1 - similarities).clip(lower=0)

dissimilarities.round(3)

1-57 (Xie_XS)  15033 (Xie_XS)  2-15 (Xie_XS)    2H2  \
1-57 (Xie_XS)                0.000           1.000          1.000  1.000   
15033 (Xie_XS)               1.000           0.000          0.910  0.945   
2-15 (Xie_XS)                1.000           0.910          0.000  0.819   
2H2                          1.000           0.945          0.819  0.000   
3C1                          0.999           1.000          1.000  0.971   
...                            ...             ...            ...    ...   
subject I (day 26)           0.697           0.497          0.411  0.549   
subject J (day 121)          0.612           0.742          0.789  0.732   
subject J (day 15)           0.817           0.876          0.845  0.675   
subject K (day 103)          0.901           0.876          0.773  0.251   
subject K (day 29)           0.884           0.879          0.827  0.652   

                       3C1  ADG-2  B38 (Xie_XS)  BD-236  BD-254  BD-319  ...  \
1-57 (Xie_XS)        0.999  0.934         1.000   1.000   1.000   1.000  ...   
15033 (Xie_XS)       1.000  0.990         0.736   0.886   0.854   0.247  ...   
2-15 (Xie_XS)        1.000  0.928         1.000   0.984   0.454   0.863  ...   
2H2                  0.971  0.985         0.761   0.523   0.630   0.845  ...   
3C1                  0.000  0.293         1.000   1.000   1.000   1.000  ...   
...                    ...    ...           ...     ...     ...     ...  ...   
subject I (day 26)   0.979  0.906         0.673   0.606   0.474   0.477  ...   
subject J (day 121)  0.877  0.811         0.684   0.713   0.808   0.730  ...   
subject J (day 15)   0.920  0.902         0.802   0.753   0.862   0.875  ...   
subject K (day 103)  0.929  0.903         0.636   0.483   0.794   0.874  ...   
subject K (day 29)   0.845  0.854         0.758   0.736   0.844   0.864  ...   

                     subject G (day 18)  subject G (day 94)  \
1-57 (Xie_XS)                     0.244               0.749   
15033 (Xie_XS)                    0.958               0.735   
2-15 (Xie_XS)                     0.797               0.780   
2H2                               0.787               0.756   
3C1                               0.974               0.858   
...                                 ...                 ...   
subject I (day 26)                0.464               0.466   
subject J (day 121)               0.386               0.039   
subject J (day 15)                0.612               0.254   
subject K (day 103)               0.608               0.418   
subject K (day 29)                0.669               0.366   

                     subject H (day 152)  subject H (day 61)  \
1-57 (Xie_XS)                      0.560               0.589   
15033 (Xie_XS)                     0.731               0.696   
2-15 (Xie_XS)                      0.542               0.585   
2H2                                0.708               0.622   
3C1                                0.971               0.965   
...                                  ...                 ...   
subject I (day 26)                 0.281               0.241   
subject J (day 121)                0.276               0.219   
subject J (day 15)                 0.501               0.357   
subject K (day 103)                0.472               0.316   
subject K (day 29)                 0.538               0.356   

                     subject I (day 102)  subject I (day 26)  \
1-57 (Xie_XS)                      0.680               0.697   
15033 (Xie_XS)                     0.553               0.497   
2-15 (Xie_XS)                      0.353               0.411   
2H2                                0.553               0.549   
3C1                                0.983               0.979   
...                                  ...                 ...   
subject I (day 26)                 0.029               0.000   
subject J (day 121)                0.396               0.400   
subject J (day 15)                 0.575     

Now do the multidimensional scaling [as described here](https://scikit-learn.org/stable/auto_examples/manifold/plot_mds.html#sphx-glr-auto-examples-manifold-plot-mds-py) to get the x and y coordinates for each antibody / serum:

In [6]:
# use multidimensional scaling to get locations of antibodies
mds = sklearn.manifold.MDS(
    n_components=2,
    metric=True,
    max_iter=3000,
    eps=1e-6,
    random_state=1,
    dissimilarity='precomputed',
    n_jobs=1,
)

mds_coords = (
    pd.DataFrame(mds.fit_transform(dissimilarities), columns=['x', 'y'])
    .assign(
        condition=dissimilarities.columns,
        xmin=lambda df: df['x'].min(),
        ymin=lambda df: df['y'].min(),
        x=lambda df: df['x'] - df['xmin'],
        y=lambda df: df['y'] - df['ymin'],
    )
    .merge(conditions_df, on='condition', how='left', validate="many_to_one")
    .drop(columns=['xmin', 'ymin', "study", "condition_alias", "condition_type"])
)

mds_coords.round(3)

x      y            condition   condition_subtype  \
0     0.868  1.515        1-57 (Xie_XS)             class 3   
1     0.162  1.120       15033 (Xie_XS)             class 1   
2     0.602  1.358        2-15 (Xie_XS)             class 2   
3     0.517  0.946                  2H2             class 1   
4     0.217  0.335                  3C1             class 4   
...     ...    ...                  ...                 ...   
1617  0.493  1.121   subject I (day 26)  convalescent serum   
1618  0.690  0.887  subject J (day 121)  convalescent serum   
1619  0.744  0.600   subject J (day 15)  convalescent serum   
1620  0.573  0.821  subject K (day 103)  convalescent serum   
1621  0.699  0.699   subject K (day 29)  convalescent serum   

                           eliciting_virus       lab  \
0     (SARS-CoV-2, pre-Omicron SARS-CoV-2)    Xie_XS   
1     (SARS-CoV-2, pre-Omicron SARS-CoV-2)    Xie_XS   
2     (SARS-CoV-2, pre-Omicron SARS-CoV-2)    Xie_XS   
3     (SARS-CoV-2, pre-Omicron SARS-CoV-2)    Xie_XS   
4     (SARS-CoV-2, pre-Omicron SARS-CoV-2)    Xie_XS   
...                                    ...       ...   
1617  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  Bloom_JD   
1618  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  Bloom_JD   
1619  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  Bloom_JD   
1620  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  Bloom_JD   
1621  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  Bloom_JD   

                  known_to_neutralize  
0                       (Wuhan-Hu-1,)  
1                       (Wuhan-Hu-1,)  
2                       (Wuhan-Hu-1,)  
3     (Wuhan-Hu-1, Omicron BA.2.12.1)  
4                       (Wuhan-Hu-1,)  
...                               ...  
1617                    (Wuhan-Hu-1,)  
1618                    (Wuhan-Hu-1,)  
1619                    (Wuhan-Hu-1,)  
1620                    (Wuhan-Hu-1,)  
1621                    (Wuhan-Hu-1,)  

[1622 rows x 7 columns]

## Read information on studies and merge into conditions data frame

In [7]:
studies = pd.read_csv('processed_data/studies.csv')

studies

study                                   citation  \
0               2021_Dong_AZ               Dong et al. Nat Micro (2021)   
1     2021_Greaney_Crowe_Abs   Greaney et al. Cell Host Microbe (2021a)   
2   2021_Greaney_HAARVI_sera   Greaney et al. Cell Host Microbe (2021b)   
3     2021_Greaney_COV2-2955                   Greaney et al. NA (2021)   
4   2021_Greaney_Rockefeller             Greaney et al. Nat Comm (2021)   
5       2021_Greaney_Moderna       Greaney et al. Sci Transl Med (2021)   
6       2021_Starr_LY-CoV555  Starr et al. Cell Reports Medicine (2021)   
7             2021_Starr_Vir                 Starr et al. Nature (2021)   
8            2021_Starr_REGN                Starr et al. Science (2021)   
9      2021_Tortorici_S2X259             Tortorici et al. Nature (2021)   
10          2022_Cao_BA2-4-5                  Cao et al. Nature (2022a)   
11          2022_Cao_Omicron                  Cao et al. Nature (2022b)   
12        2022_Greaney_B1351            Greaney et al. PLoS Path (2022)   

                                                  url  
0   https://www.nature.com/articles/s41564-021-009...  
1   https://www.sciencedirect.com/science/article/...  
2   https://www.sciencedirect.com/science/article/...  
3   https://github.com/jbloomlab/SARS-CoV-2-RBD_MA...  
4   https://www.nature.com/articles/s41467-021-244...  
5   https://stm.sciencemag.org/content/13/600/eabi...  
6          https://doi.org/10.1016/j.xcrm.2021.100255  
7   https://www.nature.com/articles/s41586-021-038...  
8   https://science.sciencemag.org/content/early/2...  
9   https://www.nature.com/articles/s41586-021-038...  
10  https://www.nature.com/articles/s41586-022-049...  
11  https://www.nature.com/articles/s41586-021-043...  
12  https://journals.plos.org/plospathogens/articl...

In [8]:
conditions_df = (
    conditions_df
    .drop(columns=['citation', 'url'], errors='ignore')
    .merge(studies, how='left', on='study', validate='many_to_one')
    )

conditions_df.head()

condition_type condition_subtype       condition condition_alias  \
0       antibody           class 1  15033 (Xie_XS)                   
1       antibody           class 1             2H2                   
2       antibody           class 1    B38 (Xie_XS)                   
3       antibody           class 1          BD-236                   
4       antibody           class 1          BD-319                   

                        eliciting_virus             study     lab  \
0  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  2022_Cao_Omicron  Xie_XS   
1  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  2022_Cao_BA2-4-5  Xie_XS   
2  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  2022_Cao_Omicron  Xie_XS   
3  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  2022_Cao_Omicron  Xie_XS   
4  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  2022_Cao_Omicron  Xie_XS   

               known_to_neutralize                   citation  \
0                    (Wuhan-Hu-1,)  Cao et al. Nature (2022b)   
1  (Wuhan-Hu-1, Omicron BA.2.12.1)  Cao et al. Nature (2022a)   
2                    (Wuhan-Hu-1,)  Cao et al. Nature (2022b)   
3                    (Wuhan-Hu-1,)  Cao et al. Nature (2022b)   
4                    (Wuhan-Hu-1,)  Cao et al. Nature (2022b)   

                                                 url  
0  https://www.nature.com/articles/s41586-021-043...  
1  https://www.nature.com/articles/s41586-022-049...  
2  https://www.nature.com/articles/s41586-021-043...  
3  https://www.nature.com/articles/s41586-021-043...  
4  https://www.nature.com/articles/s41586-021-043...

## Make interactive plots
First make plot to select condition(s) to show:

In [9]:
condition_subtypes = (conditions_df
                      ['condition_subtype']
                      .unique()
                      .tolist()
                      )

# define colors from here: https://vega.github.io/vega/docs/schemes/
# similar to Greaney et al antibody class papers
condition_subtype_colors = {'class 1': '#E52794',
                            'class 2': '#6A0DAD',
                            'class 3': '#66CCEE',
                            'class 4': '#E69F00',
                            # greens from https://www.rapidtables.com/web/color/green-color.html
                            'convalescent serum': '#006400', 
                            'Moderna vaccine serum': '#98FB98',
                            'B.1.351 convalescent plasma': '#808000',
                            }
if not set(condition_subtypes).issubset(condition_subtype_colors):
    raise ValueError('missing colors for some condition subtypes')
select_condition_subtype = alt.selection_point(fields=['condition_subtype'],
                                               # initialize to show antibodies but not sera
                                               value=[{'condition_subtype': subtype} for subtype in
                                                      conditions_df.query('condition_type == "antibody"')
                                                      ['condition_subtype'].unique()],
                                               resolve='union',
                                               empty=True,
                                               )
condition_subtype_color = alt.condition(select_condition_subtype,
                                   alt.Color('condition_subtype:N',
                                             legend=None,
                                             scale=alt.Scale(domain=condition_subtypes,
                                                             range=[condition_subtype_colors[c]
                                                                    for c in condition_subtypes]),
                                                             ),
                                   alt.value('white'),
                                   )

circle_size = 110

legend_condition_type = (
    alt.Chart(conditions_df[['condition_type', 'condition_subtype']].drop_duplicates())
    .mark_circle(size=0.7 * circle_size,
                 stroke='black',
                 strokeWidth=1)
    .encode(x=alt.X('condition_type:N',
                    axis=alt.Axis(title=['',
                                         'On each subplot, you can:',
                                         ' - click to select one item',
                                         ' - shift-click to select additional items',
                                         ' - double-click to clear selected items',
                                         ' - mouseover to see antibody/serum name',
                                         ],
                                  titleAlign='left',
                                  titleFontSize=14,
                                  titleFontWeight='normal',
                                  titleFontStyle='italic',
                                  labelFontSize=12),
                    ),
            y=alt.Y('condition_subtype:N',
                    sort=condition_subtypes,
                    axis=alt.Axis(title=None,
                                  labelFontSize=12,
                                  orient='right'),
                    ),
            color=condition_subtype_color,
            )
    .add_parameter(select_condition_subtype)
    .properties(title={'text': 'choose antibody/serum types to display',
                       'align': 'left',
                       'anchor': 'start'})
    )

(legend_condition_type).configure_view(strokeOpacity=0)

alt.Chart(...)

Encode the conditions as integers and then lookup details.
Needed to avoid some unclear problem when sorting:

In [10]:
encoded_conditions_df = (
    conditions_df
    .drop(columns="condition_type")
    .reset_index(drop=True)
    .assign(encoding=lambda x: x.index)
)

condition_encodings = encoded_conditions_df[["encoding"]]
assert len(condition_encodings) == condition_encodings["encoding"].nunique()

Make plot:

In [11]:
eliciting_viruses = sorted(dms_data.explode("eliciting_virus")["eliciting_virus"].unique())
eliciting_virus_selection = alt.selection_point(
    fields=['eliciting_virus'],
    bind=alt.binding_select(
        options=[None] + eliciting_viruses,
        labels=['all'] + eliciting_viruses,
        name="eliciting virus",
    ),
    value=[{'eliciting_virus': 'SARS-CoV-2'}]
)

labs = sorted(dms_data['lab'].unique())
lab_selection = alt.selection_point(
    fields=['lab'],
    bind=alt.binding_select(
        options=[None] + labs,
        labels=['all'] + labs,
        name="lab",
    ),
    value=[{"lab": "Bloom_JD"}]
)

known_to_neutralize_options = (
    sorted(dms_data.explode("known_to_neutralize")["known_to_neutralize"].unique())
)
known_to_neutralize_selection = alt.selection_point(
    fields=['known_to_neutralize'],
    bind=alt.binding_select(
        options=[None, *known_to_neutralize_options],
        labels=["all", *known_to_neutralize_options],
        name="known to neutralize",
   ),
)

highlight_condition = alt.selection_point(
    on='click',
    fields=['condition'],
    nearest=False,
    empty=False,
    toggle=True,
    resolve='union',
    value=[{"condition": ""}]
)

cell_height = 17  # size of cells in heat map

conditions_data = (
    alt.Chart(condition_encodings)
    .transform_lookup(
        lookup="encoding",
        from_=alt.LookupData(
            data=encoded_conditions_df,
            key="encoding",
            fields=["known_to_neutralize"],
        )
    )
    .transform_flatten(["known_to_neutralize"])
    .transform_filter(known_to_neutralize_selection)
    .transform_aggregate(encoding="mean(encoding)", groupby=["encoding"])
    .transform_lookup(
        lookup="encoding",
        from_=alt.LookupData(
            data=encoded_conditions_df,
            key="encoding",
            fields=["eliciting_virus"],
        )
    )
    .transform_flatten(["eliciting_virus"])
    .transform_filter(eliciting_virus_selection)
    .transform_aggregate(encoding="mean(encoding)", groupby=["encoding"])
    .transform_lookup(
        lookup="encoding",
        from_=alt.LookupData(
            data=encoded_conditions_df,
            key="encoding",
            fields=[
                c for c in encoded_conditions_df.columns
                if c not in {"encoding", "known_to_neutralize", "eliciting_virus"}
            ],
        )
    )
    .transform_filter(select_condition_subtype)
    .transform_filter(lab_selection)
)

# build zoom bar to zoom in condition legend
legend_condition_zoom_brush = alt.selection_interval(
                encodings=['y'],
                mark=alt.BrushConfig(stroke='black', strokeWidth=2),
                )
legend_condition_zoom_bar = (
    conditions_data
    .mark_rect()
    .encode(y=alt.Y("condition:N",
                    title='antibody / sera zoom bar',
                    axis=alt.Axis(ticks=False,
                                  labels=False,
                                  titleFontSize=12),
                    scale=alt.Scale(nice=False, zero=False),
                    sort=alt.EncodingSortField("encoding"),
                    ),
            color=condition_subtype_color,
            )
    .add_parameter(legend_condition_zoom_brush)
    .properties(height=175, width=15)
    )

condition_base = (
    conditions_data
    .add_parameter(select_condition_subtype,
                   highlight_condition,
                   known_to_neutralize_selection,
                   eliciting_virus_selection,
                   lab_selection,
                   legend_condition_zoom_brush)
    .transform_filter(legend_condition_zoom_brush)
    .properties(height={'step': cell_height},
                width=cell_height,
                )
    )

legend_condition_heatmap = (
    condition_base
    .encode(y=alt.Y('condition:N',
                    sort=alt.EncodingSortField("encoding"),
                    title=None,
                    axis=alt.Axis(orient='right',
                                  labelFontSize=11,
                                  ),
                    ),
            color=condition_subtype_color,
            strokeWidth=alt.condition(~highlight_condition,
                                      alt.value(0.5),
                                      alt.value(3)),
            stroke=alt.condition(~highlight_condition,
                                 alt.value('black'),
                                 alt.value('black')),
            )
    .mark_rect()
    )

condition_citations = (
    condition_base
    .encode(y=alt.Y('condition:N',
                    sort=alt.EncodingSortField("encoding"),
                    title=None,
                    axis=None,
                    ),
            text='citation:N',
            href='url:N'
            )
    .mark_text(align='left',
               fontSize=11,
               fontStyle='normal',
               color='darkblue',
               )
    )

condition_alias = (
    condition_base
    .encode(y=alt.Y('condition:N',
                    sort=alt.EncodingSortField("encoding"),
                    title=None,
                    axis=None,
                    ),
            text='condition_alias:N',
            )
    .mark_text(text='dms-view',
               align='left',
               fontSize=11,
               fontStyle='normal',
               )
    )

legend_condition = (
    (legend_condition_zoom_bar | alt.hconcat(legend_condition_heatmap,
                                             condition_citations,
                                             condition_alias,
                                             spacing=2)
     )
    .properties(title={'text': ['select antibody/serum by by clicking box; shift-click',
                                'citation or dms-view text to open that information']})
    )

(legend_condition_type | legend_condition).configure_view(strokeOpacity=0)

alt.HConcatChart(...)

Next make MDS plot:

In [12]:
# first add conditions encoding
mds_coords = (
    mds_coords
    .drop(columns="encoding", errors="ignore")
    .merge(
        encoded_conditions_df[["condition", "encoding"]],
        validate="many_to_one",
        how="outer",
    )
)
assert mds_coords.notnull().all().all()

mds_coords

x         y            condition   condition_subtype  \
0     0.867523  1.515217        1-57 (Xie_XS)             class 3   
1     0.162211  1.119700       15033 (Xie_XS)             class 1   
2     0.601619  1.358221        2-15 (Xie_XS)             class 2   
3     0.517172  0.945830                  2H2             class 1   
4     0.217066  0.334896                  3C1             class 4   
...        ...       ...                  ...                 ...   
1617  0.492541  1.121023   subject I (day 26)  convalescent serum   
1618  0.690335  0.887305  subject J (day 121)  convalescent serum   
1619  0.743986  0.599801   subject J (day 15)  convalescent serum   
1620  0.572512  0.821274  subject K (day 103)  convalescent serum   
1621  0.699221  0.699178   subject K (day 29)  convalescent serum   

                           eliciting_virus       lab  \
0     (SARS-CoV-2, pre-Omicron SARS-CoV-2)    Xie_XS   
1     (SARS-CoV-2, pre-Omicron SARS-CoV-2)    Xie_XS   
2     (SARS-CoV-2, pre-Omicron SARS-CoV-2)    Xie_XS   
3     (SARS-CoV-2, pre-Omicron SARS-CoV-2)    Xie_XS   
4     (SARS-CoV-2, pre-Omicron SARS-CoV-2)    Xie_XS   
...                                    ...       ...   
1617  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  Bloom_JD   
1618  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  Bloom_JD   
1619  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  Bloom_JD   
1620  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  Bloom_JD   
1621  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  Bloom_JD   

                  known_to_neutralize  encoding  
0                       (Wuhan-Hu-1,)       484  
1                       (Wuhan-Hu-1,)         0  
2                       (Wuhan-Hu-1,)       342  
3     (Wuhan-Hu-1, Omicron BA.2.12.1)         1  
4                       (Wuhan-Hu-1,)      1088  
...                               ...       ...  
1617                    (Wuhan-Hu-1,)      1617  
1618                    (Wuhan-Hu-1,)      1618  
1619                    (Wuhan-Hu-1,)      1619  
1620                    (Wuhan-Hu-1,)      1620  
1621                    (Wuhan-Hu-1,)      1621  

[1622 rows x 8 columns]

In [13]:
# size, but scaled so a unit on x and y mean the same; note
# padding added here so sizes correct
size = 180
pad = 0.04
x_extent = mds_coords['x'].max() - mds_coords['x'].min()
y_extent = mds_coords['y'].max() - mds_coords['y'].min()
y_min = mds_coords['y'].min() - pad * y_extent
y_max = mds_coords['y'].max() + pad * y_extent
x_min = mds_coords['x'].min() - pad * x_extent
x_max = mds_coords['x'].max() + pad * x_extent

mds_plot = (
    alt.Chart(condition_encodings)
    .transform_lookup(
        lookup="encoding",
        from_=alt.LookupData(
            data=mds_coords,
            key="encoding",
            fields=["known_to_neutralize"],
        )
    )
    .transform_flatten(["known_to_neutralize"])
    .transform_filter(known_to_neutralize_selection)
    .transform_aggregate(encoding="mean(encoding)", groupby=["encoding"])
    .transform_lookup(
        lookup="encoding",
        from_=alt.LookupData(
            data=mds_coords,
            key="encoding",
            fields=["eliciting_virus"],
        )
    )
    .transform_flatten(["eliciting_virus"])
    .transform_filter(eliciting_virus_selection)
    .transform_aggregate(encoding="mean(encoding)", groupby=["encoding"])
    .transform_lookup(
        lookup="encoding",
        from_=alt.LookupData(
            data=mds_coords,
            key="encoding",
            fields=[
                c for c in mds_coords.columns
                if c not in {"encoding", "known_to_neutralize", "eliciting_virus"}
            ],
        )
    )
    .transform_filter(lab_selection)
    .transform_filter(select_condition_subtype)
    .encode(x=alt.X('x:Q',
                    scale=alt.Scale(padding=0,
                                    nice=False,
                                    domain=(x_min, x_max),
                                    ),
                    axis=alt.Axis(labels=False,
                                  title=None,
                                  ticks=False,
                                  grid=False,
                                  ),
                    ),
            y=alt.Y('y:Q',
                    scale=alt.Scale(padding=0,
                                    nice=False,
                                    domain=(y_min, y_max),
                                    ),
                    axis=alt.Axis(labels=False,
                                  title=None,
                                  ticks=False,
                                  grid=False,
                                  ),
                    ),
            opacity=alt.condition(~highlight_condition, alt.value(0.3), alt.value(1)),
            stroke=alt.condition(~highlight_condition, alt.value(None), alt.value('black')),
            color=condition_subtype_color,
            tooltip=['condition:N'])
    .mark_circle(size=circle_size)
    .properties(width=size * x_extent,
                height=size * y_extent,
                title={'text': 'multidimensional scaling of antibodies/sera',
                       'subtitle': ['antibodies/sera with escape mutations at similar',
                                    'sites are positioned nearby in the plot below'],
                       'anchor': 'start',
                       'align': 'left',
                       }
                )
    .add_parameter(
        highlight_condition,
        select_condition_subtype,
        known_to_neutralize_selection,
        eliciting_virus_selection,
        lab_selection,
    )
)

# box around MDS plot: https://stackoverflow.com/a/62862229/4191652
dummy_lines = {}
for key, x, y in [('top', (x_min, x_max), (y_max, y_max)),
                  ('right', (x_max, x_max), (y_min, y_max)),
                  ]:
    dummy_lines[key] = (
        alt.Chart(pd.DataFrame({'x': x,
                                'y': y})
                  )
        .mark_line(color='black',
                   strokeWidth=0.5)
        .encode(x=alt.X('x:Q',
                        scale=alt.Scale(padding=0,
                                        nice=False,
                                        domain=(x_min, x_max),
                                        ),
                        axis=alt.Axis(labels=False,
                                      title=None,
                                      ticks=False,
                                      grid=False,
                                      ),
                        ),
                y=alt.Y('y:Q',
                        scale=alt.Scale(padding=0,
                                        nice=False,
                                        domain=(y_min, y_max),
                                        ),
                        axis=alt.Axis(labels=False,
                                      title=None,
                                      ticks=False,
                                      grid=False,
                                      ),
                        )
                )
        )
mds_plot = mds_plot + dummy_lines['top'] + dummy_lines['right']

# show the plot with legend
(
    (legend_condition_type | mds_plot | legend_condition)
    .configure_view(stroke='black')
    .configure_view(strokeOpacity=0)
)

alt.HConcatChart(...)

Next make line plots.
First, encode everything other than the actual site / escape values as in integer that we can lookup transform to the condition (antibody/sera) level values.
This dramatically shrinks size of the data:

In [14]:
dms_data_encoded = (
    dms_data[["condition", "site", "escape"]]
    .merge(encoded_conditions_df, validate="many_to_one", how="outer")
    [["encoding", "site", "escape"]]
)
assert dms_data_encoded.notnull().all().all()
assert len(dms_data_encoded) == len(dms_data_encoded.drop_duplicates())

display(encoded_conditions_df)
display(dms_data_encoded)

condition_subtype            condition condition_alias  \
0                class 1       15033 (Xie_XS)                   
1                class 1                  2H2                   
2                class 1         B38 (Xie_XS)                   
3                class 1               BD-236                   
4                class 1               BD-319                   
...                  ...                  ...             ...   
1617  convalescent serum   subject I (day 26)                   
1618  convalescent serum  subject J (day 121)                   
1619  convalescent serum   subject J (day 15)                   
1620  convalescent serum  subject K (day 103)                   
1621  convalescent serum   subject K (day 29)                   

                           eliciting_virus                     study  \
0     (SARS-CoV-2, pre-Omicron SARS-CoV-2)          2022_Cao_Omicron   
1     (SARS-CoV-2, pre-Omicron SARS-CoV-2)          2022_Cao_BA2-4-5   
2     (SARS-CoV-2, pre-Omicron SARS-CoV-2)          2022_Cao_Omicron   
3     (SARS-CoV-2, pre-Omicron SARS-CoV-2)          2022_Cao_Omicron   
4     (SARS-CoV-2, pre-Omicron SARS-CoV-2)          2022_Cao_Omicron   
...                                    ...                       ...   
1617  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  2021_Greaney_HAARVI_sera   
1618  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  2021_Greaney_HAARVI_sera   
1619  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  2021_Greaney_HAARVI_sera   
1620  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  2021_Greaney_HAARVI_sera   
1621  (SARS-CoV-2, pre-Omicron SARS-CoV-2)  2021_Greaney_HAARVI_sera   

           lab              known_to_neutralize  \
0       Xie_XS                    (Wuhan-Hu-1,)   
1       Xie_XS  (Wuhan-Hu-1, Omicron BA.2.12.1)   
2       Xie_XS                    (Wuhan-Hu-1,)   
3       Xie_XS                    (Wuhan-Hu-1,)   
4       Xie_XS                    (Wuhan-Hu-1,)   
...        ...                              ...   
1617  Bloom_JD                    (Wuhan-Hu-1,)   
1618  Bloom_JD                    (Wuhan-Hu-1,)   
1619  Bloom_JD                    (Wuhan-Hu-1,)   
1620  Bloom_JD                    (Wuhan-Hu-1,)   
1621  Bloom_JD                    (Wuhan-Hu-1,)   

                                      citation  \
0                    Cao et al. Nature (2022b)   
1                    Cao et al. Nature (2022a)   
2                    Cao et al. Nature (2022b)   
3                    Cao et al. Nature (2022b)   
4                    Cao et al. Nature (2022b)   
...                                        ...   
1617  Greaney et al. Cell Host Microbe (2021b)   
1618  Greaney et al. Cell Host Microbe (2021b)   
1619  Greaney et al. Cell Host Microbe (2021b)   
1620  Greaney et al. Cell Host Microbe (2021b)   
1621  Greaney et al. Cell Host Microbe (2021b)   

                                                    url  encoding  
0     https://www.nature.com/articles/s41586-021-043...         0  
1     https://www.nature.com/articles/s41586-022-049...         1  
2     https://www.nature.com/articles/s41586-021-043...         2  
3     https://www.nature.com/articles/s41586-021-043...         3  
4     https://www.nature.com/articles/s41586-021-043...         4  
...                                                 ...       ...  
1617  https://www.sciencedirect.com/science/article/...      1617  
1618  https://www.sciencedirect.com/science/article/...      1618  
1619  https://www.sciencedirect.com/science/article/...      1619  
1620  https://www.sciencedirect.com/science/article/...      1620  
1621  https://www.sciencedirect.com/science/article/...      1621  

[1622 rows x 10 columns]

encoding  site   escape
0           484   338  0.04456
1           484   370  0.03163
2           484   396  0.02170
3           484   444  0.03632
4           484   445  0.11140
...         ...   ...      ...
46790      1621   527  0.01916
46791      1621   528  0.03540
46792      1621   529  0.11490
46793      1621   530  0.08733
46794      1621   531  0.02767

[46795 rows x 3 columns]

Now make plot:

In [15]:
width = 800

# build base for escape plots
escape_base = (
    alt.Chart(dms_data_encoded)
    .transform_lookup(
        lookup="encoding",
        from_=alt.LookupData(
            data=encoded_conditions_df,
            key="encoding",
            fields=["known_to_neutralize"],
        )
    )
    .transform_flatten(["known_to_neutralize"])
    .transform_filter(known_to_neutralize_selection)
    .transform_aggregate(
        escape="mean(escape)",
        groupby=["encoding", "site"],
    )
    .transform_lookup(
        lookup="encoding",
        from_=alt.LookupData(
            data=encoded_conditions_df,
            key="encoding",
            fields=["eliciting_virus"],
        )
    )
    .transform_flatten(["eliciting_virus"])
    .transform_filter(eliciting_virus_selection)
    .transform_aggregate(
        escape="mean(escape)",
        groupby=["encoding", "site"],
    )
    .transform_lookup(
        lookup="encoding",
        from_=alt.LookupData(
            data=encoded_conditions_df,
            key="encoding",
            fields=["condition", "condition_subtype", "lab"],
        )
    )
    .transform_calculate(mean_over="1")
    .transform_filter(lab_selection)
    .transform_filter(select_condition_subtype)
    .encode(
        x=alt.X(
            'site:Q',
            axis=alt.Axis(grid=False),
            scale=alt.Scale(nice=False, zero=False),
        ),
    )
    .properties(width=width, height=200)
    )

# the escape line plot
escape_lines = (
    escape_base
    .encode(
        size=alt.condition(~highlight_condition, alt.value(0.75), alt.value(2)),
        opacity=alt.condition(~highlight_condition, alt.value(0.35), alt.value(1)),
        detail='encoding',  # https://github.com/altair-viz/altair/issues/985
        color=condition_subtype_color,
        y=alt.Y(
            'escape:Q',
            axis=alt.Axis(grid=False),
            impute=alt.ImputeParams(value=0, keyvals=sites),
        ),
        tooltip=['site:Q', "condition:N"],
    )
    .add_parameter(
        known_to_neutralize_selection,
        eliciting_virus_selection,
        lab_selection,
        select_condition_subtype,
        highlight_condition,
    )
    .mark_line()
    .properties(title={'text': 'escape from individual antibodies/sera'})
)

# checkbox to specify if mean for only selected antibodies or all antibody/serum types
mean_radio = alt.binding_radio(
    options=[1, 0],
    labels=["all displayed types", "just selected antibodies/sera"],
)
mean_selection = alt.selection_point(
    fields=['mean_over'],
    bind=mean_radio,
    name='calculate',
    value=[{'mean_over': 1}],
)
# plot of mean values
escape_mean = (
    escape_base
    .transform_filter(highlight_condition | (select_condition_subtype & mean_selection))
    # take mean without having to make a huge number of 0 imputations
    .transform_joinaggregate(n_conditions="distinct(encoding)")
    .transform_aggregate(
        sum_escape="sum(escape)",
        n_conditions="mean(n_conditions)",
        groupby=["site"],
    )
    .transform_calculate(mean_escape="datum.sum_escape / datum.n_conditions")
    .transform_impute(
        impute="mean_escape",
        key="site",
        value=0,
        keyvals=sites,
    )
    .mark_line(color='darkgray', point={'color': 'darkgray', 'size': 60})
    .encode(
        tooltip=[
            'site:Q',
            alt.Tooltip('mean_escape:Q', format='.2g', title='escape'),
        ],
        y=alt.Y(
            'mean_escape:Q',
            axis=alt.Axis(grid=False, title='escape'),
        ),
    )
    .add_parameter(highlight_condition, mean_selection)
    .properties(title={'text': 'mean escape over selected antibodies/sera or ' +
                               'antibody/serum types (choose with radio button below)'}
    )
)

# combine elements
escape_plot = escape_lines & escape_mean

escape_plot

alt.VConcatChart(...)

Now combine the antibody MDS and escape plots:

In [16]:
chart = (
    (((legend_condition_type | mds_plot) & escape_plot) | legend_condition)
    .configure(padding={'left': 5,
                        'right': 60,
                        'top': 5,
                        'bottom': 5})
    .configure_view(strokeOpacity=0)
)

chartfile = 'docs/_includes/chart.html'
os.makedirs(os.path.dirname(chartfile), exist_ok=True)
print(f"Saving chart to {chartfile}")
chart.save(chartfile)

chart

Saving chart to docs/_includes/chart.html


alt.HConcatChart(...)